In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import descartes
import geopandas as gpd
import numpy as np
from shapely.geometry import Point, Polygon
import folium
import branca

In [4]:
community_map = gpd.read_file('SHP/Boston_SHP/Original_Shp/neighbourhoods.geojson')
community_map = community_map.rename(columns={'neighbourhood':'community'})

df = pd.read_csv('./Data/Boston_Crimes.csv')
crs = {'init' : 'epsg:4326'}
df = df.dropna(subset=['LATITUDE'])
df= df[df['LATITUDE'] != 0]

geometry = [Point(xy) for xy in zip(df["LONGITUDE"], df["LATITUDE"])]
geometry[:3]


geo_df = gpd.GeoDataFrame(df, crs = crs, geometry = geometry)

C:\Users\Saajid\AppData\Local\Temp\ipykernel_26452\3616620412.py:4: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('./Data/Boston_Crimes.csv')
C:\Users\Saajid\anaconda3\envs\geopandas\lib\site-packages\pyproj\crs\crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)


In [3]:
# community_map.head()

In [5]:
# taken from https://towardsdatascience.com/tagging-a-location-to-a-shapefile-area-using-geopandas-5d74336128bf
geo_df['community'] = ''
for idx in range(community_map.shape[0]):
    #For every lat/long, find if they reside within a community
    pip = geo_df.within(community_map.loc[idx, 'geometry'])
    if pip.sum() > 0:
        geo_df.loc[pip, 'community']  = community_map.loc[idx, 'community']

In [6]:
# geo_df = gpd.read_file("SHP/Boston_SHP/Summarized_Shp/BostonCrime.shp")

In [6]:
# taking group by and then reverting back to data frame to use
# https://technology.amis.nl/data-analytics/convert-groupby-result-on-pandas-data-frame-into-a-data-frame-using-to_frame/
crimebycommunity = geo_df.groupby(['community'])['community'].count().to_frame(name = 'count').reset_index()


crimebycommunity['community'].replace('', np.nan, inplace=True)
crimebycommunity = crimebycommunity.dropna(subset=['community'])


map_and_stats = community_map.merge(crimebycommunity, on="community")

map_and_stats_2 = map_and_stats[['community','geometry','count']]

In [7]:
#Exporting after the groupby summarization
map_and_stats_2.to_file("SHP/Boston_SHP/Summarized_Shp/BostonCrime.shp")

C:\Users\Saajid\anaconda3\envs\geopandas\lib\site-packages\geopandas\io\file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


In [8]:
map_and_stats_2 = gpd.read_file("SHP/Boston_SHP/Summarized_Shp/BostonCrime.shp")

In [9]:
# https://vverde.github.io/blob/interactivechoropleth.html

x_map = map_and_stats_2.centroid.x.mean()
y_map = map_and_stats_2.centroid.y.mean()



mymap = folium.Map(location=[y_map, x_map], zoom_start=12,tiles=None)
folium.TileLayer('CartoDB positron',name="Light Map",control=False).add_to(mymap)


myscale = (map_and_stats_2['count'].quantile((0,0.25,0.9,1))).tolist()

C:\Users\Saajid\AppData\Local\Temp\ipykernel_26452\136192827.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  x_map = map_and_stats_2.centroid.x.mean()
C:\Users\Saajid\AppData\Local\Temp\ipykernel_26452\136192827.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  y_map = map_and_stats_2.centroid.y.mean()


In [10]:
mymap.choropleth(
geo_data=map_and_stats_2,
name='Choropleth',
data=map_and_stats_2,
columns=['community','count'],
key_on="feature.properties.community",
fill_color='Reds', #https://matplotlib.org/3.5.1/tutorials/colors/colormaps.html          sequential color maps
threshold_scale=myscale,
fill_opacity=0.5,
line_opacity=0.2,
legend_name='Crime Count',
smooth_factor=0
)

C:\Users\Saajid\anaconda3\envs\geopandas\lib\site-packages\folium\folium.py:409: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [11]:
mymap

In [12]:
style_function = lambda x: {'fillColor': '#ffffff',
                            'color':'#000000',
                            'fillOpacity': 0.1,
                            'weight': 0.1}

highlight_function = lambda x: {'fillColor': '#000000',
                                'color':'#000000',
                                'fillOpacity': 0.50,
                                'weight': 0.1}

In [13]:
CrimeCount = folium.features.GeoJson(
    map_and_stats_2,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['community','count'],
        aliases=['Neighborhood: ','Count of Crimes '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")
    )
)
mymap.add_child(CrimeCount)
mymap.keep_in_front(CrimeCount)
folium.LayerControl().add_to(mymap)

In [14]:
#this map should have the interactivity now
mymap

In [15]:
df_airbnb = pd.read_csv('./Data/Boston_listings.csv')


airbnb_locations = df_airbnb[['latitude','longitude']]
airbnb_list = airbnb_locations.values.tolist()

In [16]:
df_airbnb.head()

id                         listing_url     scrape_id last_scraped  \
0   3781   https://www.airbnb.com/rooms/3781  2.020000e+13   12/17/2021   
1   5506   https://www.airbnb.com/rooms/5506  2.020000e+13   12/17/2021   
2   6695   https://www.airbnb.com/rooms/6695  2.020000e+13   12/17/2021   
3   8789   https://www.airbnb.com/rooms/8789  2.020000e+13   12/17/2021   
4  10730  https://www.airbnb.com/rooms/10730  2.020000e+13   12/17/2021   

                                  name  \
0            HARBORSIDE-Walk to subway   
1     ** Private! Minutes to center!**   
2           Home Away from Home! Condo   
3  Curved Glass Studio/1bd facing Park   
4       Bright 1bed facing Golden Dome   

                                         picture_url  host_id  \
0  https://a0.muscache.com/pictures/24670/b2de044...     4804   
1  https://a0.muscache.com/pictures/miso/Hosting-...     8229   
2  https://a0.muscache.com/pictures/38ac4797-e7a4...     8229   
3  https://a0.muscache.com/pictures/32210/7fdd2fd...    26988   
4  https://a0.muscache.com/pictures/miso/Hosting-...    26988   

                                  host_url host_name host_since  ...  \
0   https://www.airbnb.com/users/show/4804     Frank  12/3/2008  ...   
1   https://www.airbnb.com/users/show/8229     Terry  2/19/2009  ...   
2   https://www.airbnb.com/users/show/8229     Terry  2/19/2009  ...   
3  https://www.airbnb.com/users/show/26988      Anne  7/22/2009  ...   
4  https://www.airbnb.com/users/show/26988      Anne  7/22/2009  ...   

  review_scores_communication review_scores_location review_scores_value  \
0                        4.95                   4.86                4.90   
1                        4.89                   4.54                4.78   
2                        4.95                   4.48                4.70   
3                        4.96                   4.96                4.56   
4                        4.92                   4.96                4.43   

                      license instant_bookable calculated_host_listings_count  \
0                         NaN                f                              1   
1  Approved by the government                f                             10   
2                   STR446650                f                             10   
3                         NaN                f                              6   
4                         NaN                f                              6   

  calculated_host_listings_count_entire_homes  \
0                                           1   
1                                          10   
2                                          10   
3                                           6   
4                                           6   

  calculated_host_listings_count_private_rooms  \
0                                            0   
1                                            0   
2                                            0   
3                                            0   
4                                            0   

  calculated_host_listings_count_shared_rooms  reviews_per_month  
0                                           0               0.27  
1                                           0               0.71  
2                                           0               0.77  
3                                           0               0.28  
4                                           0               0.21  

[5 rows x 72 columns]

In [17]:
def popup_html(row_num, df_airbnb):
    i = row_num
    name=df_airbnb['name'].iloc[i]
    price=df_airbnb['price'].iloc[i]
    roomtype=df_airbnb['room_type'].iloc[i]


    left_col_color = "#19a7bd"
    right_col_color = "#f2f0d3"

    html = """<!DOCTYPE html>
<html>

<head>
<h4 style="margin-bottom:10"; width="200px">{}</h4>""".format(name) + """

</head>
    <table style="height: 20px; width: 200px; border:1px solid black">
<tbody>
<tr style = "border:1px solid black">
<td style = "border:1px solid black">Price Per Night:</td>
<td style = "border:1px solid black">&nbsp; {}</td>""" .format(price) + """
</tr>

<tr style = "border:1px solid black">
<td style = "border:1px solid black">Room Type:</td>
<td style = "border:1px solid black">&nbsp; {}</td>""" .format(roomtype) + """
</tr>

</tbody>
</table>
</html>
"""
    return html

In [18]:
# set price to 200 for testing
price = 200
df_airbnb_price_filtered = df_airbnb[df_airbnb.price==price]
rows = len(df_airbnb_price_filtered)
#https://georgetsilva.github.io/posts/mapping-points-with-folium/
#https://towardsdatascience.com/folium-map-how-to-create-a-table-style-pop-up-with-html-code-76903706b88a
for point in range(0,rows):
    i = point
    html = popup_html(i,df_airbnb_price_filtered)
    iframe = branca.element.IFrame(html=html,width=200,height=200)
    popup = folium.Popup(folium.Html(html, script=True), max_width=500)
    folium.Marker(airbnb_list[point], popup).add_to(mymap)

In [19]:
mymap

In [19]:
# if you want to save html locally
# mymap.save("index_Chicago.html") 